# Explaining the differences between ven and vxy
How to explain the difference in vxy-ven time series and spectra observed in diag_comparaison_va.ipynb and diag_spectra_analysis.ipynb ?

In [1]:
import os
from glob import glob

import numpy as np
import pandas as pd
import xarray as xr
import dask.dataframe as dd
import dask.array as da

# import cartopy.crs as ccrs
# import cartopy.feature as cfeature
# import geopandas as gpd
from shapely.geometry import Polygon

%matplotlib inline
from matplotlib import pyplot as plt
import hvplot.pandas
import holoviews as hv


import drifters.utils as ut
import pynsitu as pin

from dask.delayed import delayed

import GDP_lib as gdp

from GDP_lib import root_dir

In [2]:
from dask.distributed import Client

if True:
    from dask_jobqueue import PBSCluster
    from dask.distributed import Client

    # cluster = PBSCluster()
    # w = cluster.scale(jobs=3) # 2 not enough for lon, lat, year, binning
    cluster = PBSCluster(cores=3, processes=3, walltime="04:00:00")
    w = cluster.scale(jobs=3)
else:
    from dask.distributed import LocalCluster

    cluster = LocalCluster()

client = Client(cluster)
client

/home1/datahome/mdemol/.miniconda3/envs/mdenv/lib/python3.9/site-packages/dask_jobqueue/core.py:237: FutureWarning: extra has been renamed to worker_extra_args. You are still using it (even if only set to []; please also check config files). If you did not set worker_extra_args yet, extra will be respected for now, but it will be removed in a future release. If you already set worker_extra_args, extra is ignored and you can remove it.
  warnings.warn(warn, FutureWarning)
/home1/datahome/mdemol/.miniconda3/envs/mdenv/lib/python3.9/site-packages/dask_jobqueue/core.py:255: FutureWarning: job_extra has been renamed to job_extra_directives. You are still using it (even if only set to []; please also check config files). If you did not set job_extra_directives yet, job_extra will be respected for now, but it will be removed in a future release. If you already set job_extra_directives, job_extra is ignored and you can remove it.
  warnings.warn(warn, FutureWarning)
/home1/datahome/mdemol/.min

<Client: 'tcp://10.148.0.69:56544' processes=0 threads=0, memory=0 B>

In [3]:
# parquet_argos = os.path.join(root_dir, "argos_av_time.parquet")
parquet_gps = os.path.join(root_dir, "gps_av_time_corrected.parquet")

In [4]:
df_gps = dd.read_parquet(parquet_gps).reset_index().set_index("id").persist()
# df_argos = dd.read_parquet(parquet_argos).reset_index().set_index("id").persist()

In [5]:
df = df_gps.copy()

_____
## Find trajectories where $\frac{ven}{vxy}<0.5$ and $\frac{ven}{vxy}>2$

In [42]:
a = 20
dfg_ = df_gps.groupby("id").max()

dfg_["ratio_enxy"] = abs(dfg_["aen"]) / abs(dfg_["axy"])

id_no_pb = dfg_[
    (dfg_.ratio_enxy > 1 / a) & (dfg_.ratio_enxy < a)
].index.values.compute()

# id of trajectories with pb
id_gps = dfg_[(dfg_.ratio_enxy < 1 / a) | (dfg_.ratio_enxy > a)].index.values.compute()

dfg = df_gps.loc[id_gps].repartition(partition_size="100MB")
dfg_no_pb = df_gps.loc[id_no_pb].repartition(partition_size="100MB")

In [43]:
len(id_gps)

49

In [44]:
len(dfg)

382610

In [45]:
len(df_gps)

41316140

In [46]:
import hvplot.pandas
import holoviews as hv

list_id = list(dfg.get_partition(0).compute().groupby("id").groups.keys())
_id = list_id[1]  # CHANGE INT HERE TO SEE AN OTHER TRAJECTORY
grp_id = dfg.get_partition(0).groupby("id").get_group(_id).set_index("time").compute()

hvplot = (
    grp_id["x"].hvplot(grid=True)
    + grp_id["y"].hvplot(grid=True)
    + grp_id["ve"].hvplot(grid=True) * grp_id["vex"].hvplot(grid=True)
    + grp_id["vn"].hvplot(grid=True) * grp_id["vny"].hvplot(grid=True)
    + grp_id["ae"].hvplot(grid=True) * grp_id["aex"].hvplot(grid=True)
    + grp_id["an"].hvplot(grid=True) * grp_id["any"].hvplot(grid=True)
)
layout = hv.Layout(hvplot).cols(2)
# print((df_gps.gap.groupby('id').max()[_id]/3600).compute())
layout

:Layout
   .Curve.X     :Curve   [time]   (x)
   .Curve.Y     :Curve   [time]   (y)
   .Overlay.I   :Overlay
      .Curve.Ve  :Curve   [time]   (ve)
      .Curve.Vex :Curve   [time]   (vex)
   .Overlay.II  :Overlay
      .Curve.Vn  :Curve   [time]   (vn)
      .Curve.Vny :Curve   [time]   (vny)
   .Overlay.III :Overlay
      .Curve.Ae  :Curve   [time]   (ae)
      .Curve.Aex :Curve   [time]   (aex)
   .Overlay.IV  :Overlay
      .Curve.An  :Curve   [time]   (an)
      .Curve.Any :Curve   [time]   (any)

Problems before or after hole in the time series -> need to remove last or first values 
____
## Test to remove problematic values near holes 
- near hole by shifting
- only problemetic values > v 

In [47]:
cluster.close()

/home1/datahome/mdemol/.miniconda3/envs/mdenv/lib/python3.9/site-packages/dask_jobqueue/core.py:237: FutureWarning: extra has been renamed to worker_extra_args. You are still using it (even if only set to []; please also check config files). If you did not set worker_extra_args yet, extra will be respected for now, but it will be removed in a future release. If you already set worker_extra_args, extra is ignored and you can remove it.
  warnings.warn(warn, FutureWarning)
/home1/datahome/mdemol/.miniconda3/envs/mdenv/lib/python3.9/site-packages/dask_jobqueue/core.py:255: FutureWarning: job_extra has been renamed to job_extra_directives. You are still using it (even if only set to []; please also check config files). If you did not set job_extra_directives yet, job_extra will be respected for now, but it will be removed in a future release. If you already set job_extra_directives, job_extra is ignored and you can remove it.
  warnings.warn(warn, FutureWarning)
/home1/datahome/mdemol/.min

___
#
___
#
___
